# Face Recognition using CNN

https://www.freecodecamp.org/news/how-to-train-your-own-faceid-cnn-using-tensorflow-eager-execution-6905afe4fd5a/

## Import Necessary Dependacies

In [1]:
import os
import time
import cv2

import numpy as np
import pandas as pd

import tensorflow as tf
from tensorflow.keras import layers
from tensorflow.keras.models import Sequential

from sklearn.model_selection import train_test_split

from tqdm import tqdm

# Enable GPU acceleration
physical_devices = tf.config.list_physical_devices('GPU')
if physical_devices:
    tf.config.experimental.set_memory_growth(physical_devices[0], True)



## Paths

In [2]:
IMAGES_PATH = "data/img_align_celeba/"
LABELS_PATH = "data/list_bbox_celeba.txt"

## Load the data

In [3]:
# Load the bounding box labels
bbox_data = pd.read_csv(LABELS_PATH, delim_whitespace=True)


In [4]:
# Create image paths
image_paths = [os.path.join(IMAGES_PATH, filename) for filename in bbox_data['image_id']]
print("image_paths: {}".format(image_paths))

image_paths: ['data/img_align_celeba/000001.jpg', 'data/img_align_celeba/000002.jpg', 'data/img_align_celeba/000003.jpg', 'data/img_align_celeba/000004.jpg', 'data/img_align_celeba/000005.jpg', 'data/img_align_celeba/000006.jpg', 'data/img_align_celeba/000007.jpg', 'data/img_align_celeba/000008.jpg', 'data/img_align_celeba/000009.jpg', 'data/img_align_celeba/000010.jpg', 'data/img_align_celeba/000011.jpg', 'data/img_align_celeba/000012.jpg', 'data/img_align_celeba/000013.jpg', 'data/img_align_celeba/000014.jpg', 'data/img_align_celeba/000015.jpg', 'data/img_align_celeba/000016.jpg', 'data/img_align_celeba/000017.jpg', 'data/img_align_celeba/000018.jpg', 'data/img_align_celeba/000019.jpg', 'data/img_align_celeba/000020.jpg', 'data/img_align_celeba/000021.jpg', 'data/img_align_celeba/000022.jpg', 'data/img_align_celeba/000023.jpg', 'data/img_align_celeba/000024.jpg', 'data/img_align_celeba/000025.jpg', 'data/img_align_celeba/000026.jpg', 'data/img_align_celeba/000027.jpg', 'data/img_alig

In [5]:
# Create a dataset of image paths
images_ds = tf.data.Dataset.from_tensor_slices(image_paths).batch(32)
print("images_ds: {}".format(images_ds))

# Load and preprocess images
def load_and_preprocess_image(image_path):
    image = tf.io.read_file(image_path)
    image = tf.image.decode_jpeg(image, channels=3)
    image = tf.image.resize(image, [224, 224])
    image = tf.cast(image, tf.float32)
    return image

images_ds = images_ds.map(lambda x: tf.map_fn(lambda y: load_and_preprocess_image(y), x, dtype=tf.float32))
print("images_ds: {}".format(images_ds))

images_ds = images_ds.map(lambda x: tf.concat(x, axis=0))
print("images_ds: {}".format(images_ds))


images_ds: <BatchDataset element_spec=TensorSpec(shape=(None,), dtype=tf.string, name=None)>
Instructions for updating:
Use fn_output_signature instead
images_ds: <MapDataset element_spec=TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None)>
images_ds: <MapDataset element_spec=TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None)>


In [6]:
# # Convert the dataset to a numpy array
# images_ds = np.array(list(images_ds.as_numpy_iterator()))
# print("images_ds: {}".format(images_ds))

# # Save the dataset
# np.save("data/images_ds.npy", images_ds)

In [9]:
# Normalize the pixel values between 0 and 1

images_ds = images_ds.map(lambda x: x / 255.0)


In [10]:
# Extract the bounding box coordinates from the label data
bbox_coordinates = bbox_data[['x_1', 'y_1', 'width', 'height']].values

## Splitting the data

In [12]:
# Split the data into training and validation sets
train_images, val_images, train_bboxes, val_bboxes = train_test_split(images_ds, bbox_coordinates, test_size=0.2, random_state=42)

TypeError: Singleton array array(<MapDataset element_spec=TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None)>,
      dtype=object) cannot be considered a valid collection.

## Building the model

In [ ]:
model = tf.keras.models.Sequential([
    tf.keras.layers.Con((21 * 2, )),
    tf.keras.layers.Dropout(0.0),
    tf.keras.layers.Dense(32, activation='relu'),
    tf.keras.layers.Dropout(0.0),
    tf.keras.layers.Dense(32, activation='relu'),
    tf.keras.layers.Dropout(0.0),
    tf.keras.layers.Dense(16, activation='relu'),
    tf.keras.layers.Dense(NUM_CLASSES, activation='softmax')
])

model = Sequential()
model.add(layers.Conv2D(32, (3, 3), activation='relu', input_shape=(224, 224, 3)))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Conv2D(64, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Conv2D(128, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Flatten())
model.add(layers.Dense(64, activation='relu'))
model.add(layers.Dense(4))  # Output layer with 4 units for bounding box coordinates (x, y, width, height)

In [ ]:
model.summar